# Lecture 11: Advanced Data Processing - JSON, Excel, and NumPy Introduction

## Learning Objectives

By the end of this interactive notebook, you will be able to:

1. **Master advanced JSON** complex structures, APIs, validation, error handling
2. **Work with Excel files** reading, writing, multiple sheets, formatting with pandas
3. **Understand NumPy fundamentals** arrays vs lists, performance benefits, basic operations
4. **Convert between formats** JSON to Excel, CSV to Excel, array to DataFrame
5. **Build data pipelines** integrating multiple formats for analysis

Let's begin our journey into advanced data processing with modern Python tools!

## Setup and Imports

We'll be working with three powerful Python libraries today. The json module is built into Python and handles JavaScript Object Notation data - the standard format for web APIs and configuration files. pandas (which we previewed in Lecture 10) provides Excel file capabilities and data manipulation tools. NumPy gives us high-performance arrays for numerical computing. By convention, we import pandas as 'pd' and NumPy as 'np' - these aliases are universally recognized in the data science community.

In [ ]:
# Import required libraries
import json
import pandas as pd
import numpy as np
from datetime import datetime
import os

# Verify imports
print("Libraries imported successfully!")
print(f"pandas version: {pd.__version__}")
print(f"NumPy version: {np.__version__}")

## Part 1: Advanced JSON Processing

### Understanding Complex JSON Structures

In Lecture 10, you learned basic JSON with simple dictionaries and lists. Real-world JSON from APIs and modern applications contains deeply nested structures that mirror complex relationships. Think of JSON like a filing system where folders can contain other folders, documents, or lists of items. Social media posts, for example, have author information (a folder), content details (another folder), and arrays of comments (lists). Let's explore how to work with these sophisticated data structures.

In [ ]:
# Create a complex JSON structure representing a social media post
social_post = {
    "id": "post_12345",
    "author": {
        "username": "alice_dev",
        "name": "Alice Johnson",
        "verified": True,
        "followers": 1250
    },
    "content": {
        "text": "Just learned advanced JSON processing!",
        "media": [
            {"type": "image", "url": "img1.jpg"}
        ]
    }
}

The structure above represents real-world JSON complexity. Notice how the author information is nested inside the main post object, and the media is an array of objects. This hierarchical organization lets us represent relationships naturally - the author "belongs to" the post, and multiple media items can be attached to the content.

In [ ]:
# Pretty print the JSON to see its structure clearly
print("Social Media Post JSON:")
print(json.dumps(social_post, indent=2))

# Access nested data
author_name = social_post["author"]["name"]
print(f"\nPost author: {author_name}")

### Safe JSON Navigation

When working with JSON from external sources like web APIs, you can't always trust the structure will be exactly what you expect. Missing fields, null values, or changed structures can crash your program. Just like checking if a key exists in a dictionary, we need defensive programming techniques for JSON. Here's a safe way to navigate nested structures without risking KeyError exceptions.

In [ ]:
def safe_get_nested(data, keys, default=None):
    """Safely navigate nested dictionaries."""
    for key in keys:
        if isinstance(data, dict):
            data = data.get(key, default)
        else:
            return default
    return data

# Safe access examples
followers = safe_get_nested(social_post, ["author", "followers"])
bio = safe_get_nested(social_post, ["author", "bio"], "No bio")
print(f"Followers: {followers}")
print(f"Bio: {bio}")

### Exercise 1: Navigate Complex JSON

You have a JSON structure representing a product from an e-commerce API. Extract the price, first category name, and check if it's in stock. Use safe navigation to handle potential missing fields.

In [ ]:
# E-commerce product JSON
product = {
    "id": "PROD-789",
    "name": "Wireless Headphones",
    "pricing": {
        "regular_price": 79.99,
        "sale_price": 59.99
    },
    "categories": [
        {"id": 1, "name": "Electronics"},
        {"id": 2, "name": "Audio"}
    ],
    "inventory": {"in_stock": True, "quantity": 45}
}

# TODO: Extract sale price, first category name, and stock status
# Your code here:

In [ ]:
# Solution 1
# Extract required information safely
sale_price = safe_get_nested(product, ["pricing", "sale_price"], 0)
first_category = safe_get_nested(product, ["categories", 0, "name"], "Unknown")
in_stock = safe_get_nested(product, ["inventory", "in_stock"], False)

print(f"Sale Price: ${sale_price}")
print(f"Category: {first_category}")
print(f"In Stock: {in_stock}")

### JSON File Operations with Error Handling

JSON files are everywhere - configuration files, API responses saved for testing, and data exports. When loading JSON from files, many things can go wrong: the file might not exist, it could contain invalid JSON syntax, or have unexpected content. Professional code always handles these possibilities gracefully, providing helpful error messages instead of crashing.

In [ ]:
def load_json_safely(filename):
    """Load JSON with comprehensive error handling."""
    try:
        with open(filename, 'r') as file:
            data = json.load(file)
        return data, None
    except FileNotFoundError:
        return None, f"File not found: {filename}"
    except json.JSONDecodeError as e:
        return None, f"Invalid JSON at line {e.lineno}: {e.msg}"
    except Exception as e:
        return None, f"Unexpected error: {e}"

Let's create a sample JSON file and practice loading it safely. This pattern of creating data, saving it, and loading it back is common when working with APIs - you might save responses for offline testing or debugging.

In [ ]:
# Create and save a configuration file
config = {
    "app_name": "DataProcessor",
    "version": "2.0",
    "settings": {
        "max_workers": 4,
        "timeout": 30,
        "features": ["json", "excel", "numpy"]
    }
}

# Save to file
with open('app_config.json', 'w') as f:
    json.dump(config, f, indent=2)
print("Configuration saved!")

In [ ]:
# Load the configuration safely
loaded_config, error = load_json_safely('app_config.json')

if error:
    print(f"Error: {error}")
else:
    print("Configuration loaded successfully!")
    print(f"App: {loaded_config['app_name']} v{loaded_config['version']}")
    print(f"Features: {', '.join(loaded_config['settings']['features'])}")

## Part 2: Excel File Handling with pandas

### Introduction to Excel Files in Python

Excel files are the universal language of business data. Unlike CSV files which only store raw data, Excel files can contain multiple worksheets, formulas, formatting, and charts. pandas makes working with Excel files almost as easy as CSVs, but with all the extra capabilities. Think of an Excel file as a notebook with multiple pages, where each page (worksheet) can contain a different table of data.

In [ ]:
# Create sample student data for our Excel workbook
students_data = {
    'StudentID': ['S001', 'S002', 'S003', 'S004'],
    'Name': ['Alice', 'Bob', 'Carol', 'David'],
    'Major': ['CS', 'Math', 'CS', 'Physics'],
    'Year': [3, 2, 4, 2]
}

# Convert to DataFrame
students_df = pd.DataFrame(students_data)
print("Students DataFrame:")
print(students_df)

In [ ]:
# Create grades data for a second sheet
grades_data = {
    'StudentID': ['S001', 'S001', 'S002', 'S002'],
    'Course': ['Python', 'DataSci', 'Python', 'Stats'],
    'Grade': [95, 88, 87, 92],
    'Semester': ['Fall2024', 'Fall2024', 'Fall2024', 'Fall2024']
}

grades_df = pd.DataFrame(grades_data)
print("\nGrades DataFrame:")
print(grades_df)

### Writing Excel Files with Multiple Sheets

The ExcelWriter context manager is your gateway to creating professional Excel files. Just like using 'with open()' for text files ensures proper file handling, ExcelWriter manages the Excel file creation process. You can add multiple sheets, each with different data, creating organized workbooks that business users love. The context manager ensures the file is properly saved and closed even if an error occurs.

In [ ]:
# Create an Excel file with multiple sheets
with pd.ExcelWriter('student_records.xlsx', engine='openpyxl') as writer:
    # Write each DataFrame to a different sheet
    students_df.to_excel(writer, sheet_name='Students', index=False)
    grades_df.to_excel(writer, sheet_name='Grades', index=False)
    
    print("Excel file created with 2 sheets!")
    print("Sheets: 'Students' and 'Grades'")

Now let's add a summary sheet that calculates statistics from our data. This demonstrates how Excel files can contain both raw data and processed results, making them perfect for reports that non-programmers can understand and use.

In [ ]:
# Calculate summary statistics
grade_summary = grades_df.groupby('StudentID')['Grade'].agg(['mean', 'count'])
grade_summary.columns = ['Average Grade', 'Number of Courses']

# Add summary to Excel file
with pd.ExcelWriter('student_report.xlsx', engine='openpyxl') as writer:
    students_df.to_excel(writer, sheet_name='Students', index=False)
    grades_df.to_excel(writer, sheet_name='Grades', index=False)
    grade_summary.to_excel(writer, sheet_name='Summary')
    
print("Created comprehensive report with summary!")

### Reading Excel Files

Reading Excel files is just as important as writing them. You might receive data from colleagues, download reports from systems, or need to process existing spreadsheets. pandas can read specific sheets or all sheets at once, giving you flexibility in how you work with the data. Let's explore different ways to read Excel files.

In [ ]:
# Read a specific sheet from Excel
students_from_excel = pd.read_excel('student_report.xlsx', 
                                   sheet_name='Students')
print("Students data from Excel:")
print(students_from_excel)

# Check what sheets are available
excel_file = pd.ExcelFile('student_report.xlsx')
print(f"\nAvailable sheets: {excel_file.sheet_names}")

In [ ]:
# Read all sheets into a dictionary
all_sheets = pd.read_excel('student_report.xlsx', sheet_name=None)

print("Loaded all sheets:")
for sheet_name, sheet_data in all_sheets.items():
    print(f"\n{sheet_name} - {len(sheet_data)} rows")
    print(sheet_data.head(2))  # Show first 2 rows

### Exercise 2: Create a Sales Report

Create an Excel report with two sheets: 'Sales Data' containing product sales, and 'Summary' showing total sales per product. This exercise combines DataFrame creation, grouping, and multi-sheet Excel writing.

In [ ]:
# Sales data
sales_data = {
    'Date': ['2025-01-01', '2025-01-01', '2025-01-02', '2025-01-02'],
    'Product': ['Laptop', 'Mouse', 'Laptop', 'Keyboard'],
    'Quantity': [2, 5, 1, 3],
    'Price': [999.99, 29.99, 999.99, 79.99]
}

# TODO: Create DataFrame, calculate total sales per product,
# and save both to Excel file 'sales_report.xlsx'
# Your code here:

In [ ]:
# Solution 2
# Create sales DataFrame
sales_df = pd.DataFrame(sales_data)
sales_df['Total'] = sales_df['Quantity'] * sales_df['Price']

# Create summary
summary_df = sales_df.groupby('Product').agg({
    'Quantity': 'sum',
    'Total': 'sum'
}).round(2)

# Write to Excel
with pd.ExcelWriter('sales_report.xlsx') as writer:
    sales_df.to_excel(writer, sheet_name='Sales Data', index=False)
    summary_df.to_excel(writer, sheet_name='Summary')

print("Sales report created successfully!")

## Part 3: NumPy Array Fundamentals

### Why NumPy Arrays Matter

Imagine you need to add 1 to every number in a list of one million values. With a Python list, you'd need a loop that visits each element individually - like a postal worker delivering mail to each house one by one. NumPy arrays work differently - they process all elements simultaneously, like announcing over a loudspeaker that everyone should step forward. This parallel processing makes NumPy 50-100 times faster for numerical operations.

In [ ]:
import time

# Create list and array with same data
size = 100000
python_list = list(range(size))
numpy_array = np.arange(size)

print(f"Created list and array with {size:,} elements")

In [ ]:
# Time list operation
start = time.time()
list_result = [x * 2 for x in python_list]
list_time = time.time() - start

# Time array operation  
start = time.time()
array_result = numpy_array * 2
array_time = time.time() - start

print(f"List time: {list_time:.4f} seconds")
print(f"Array time: {array_time:.4f} seconds")
print(f"NumPy is {list_time/array_time:.0f}x faster!")

### Creating and Using Arrays

NumPy arrays are like lists with superpowers. You can create them from existing lists, generate them with special functions, or load them from files. The key difference is that arrays have a fixed type (all integers or all floats) which enables their speed. Think of arrays as specialized containers optimized for numerical data, while lists are general-purpose containers that can hold anything.

In [ ]:
# Create arrays different ways
from_list = np.array([1.5, 2.0, 3.5, 4.0, 5.5])
zeros = np.zeros(5)  # Five zeros
ones = np.ones(5)    # Five ones
sequence = np.arange(0, 10, 2)  # 0, 2, 4, 6, 8

print("From list:", from_list)
print("Zeros:", zeros)
print("Sequence:", sequence)

The real magic of arrays comes from vectorized operations. Instead of writing loops, you can apply operations to entire arrays at once. This isn't just convenient - it's much faster because NumPy executes these operations in optimized C code rather than Python loops.

In [ ]:
# Vectorized operations - no loops needed!
temperatures_f = np.array([72, 68, 75, 71, 78])

# Convert all to Celsius at once
temperatures_c = (temperatures_f - 32) * 5/9

print("Fahrenheit:", temperatures_f)
print("Celsius:", temperatures_c.round(1))
print(f"Average temp: {temperatures_c.mean():.1f}°C")

### Array Indexing and Selection

NumPy provides powerful ways to select data. Boolean indexing lets you filter arrays using conditions - incredibly useful for finding values that meet certain criteria. Instead of loops with if statements, you create a mask and apply it instantly. This is like using a filter to find all red marbles in a jar instead of checking each marble one by one.

In [ ]:
# Boolean indexing example
scores = np.array([88, 92, 79, 95, 85, 77, 90])

# Find scores >= 90 (A grades)
a_grades = scores[scores >= 90]
print("All scores:", scores)
print("A grades:", a_grades)
print(f"Number of A grades: {len(a_grades)}")

### Exercise 3: Grade Analysis

You have an array of test scores. Use NumPy to find the average, identify failing scores (< 60), and calculate what percentage of students passed.

In [ ]:
# Test scores
test_scores = np.array([45, 78, 82, 91, 55, 88, 95, 73, 60, 85])

# TODO: Calculate average, find failing scores, compute pass rate
# Your code here:

In [ ]:
# Solution 3
# Calculate statistics
average = test_scores.mean()
failing = test_scores[test_scores < 60]
passing = test_scores[test_scores >= 60]
pass_rate = (len(passing) / len(test_scores)) * 100

print(f"Class average: {average:.1f}")
print(f"Failing scores: {failing}")
print(f"Pass rate: {pass_rate:.0f}%")

## Part 4: Data Pipeline Integration

### Building an ETL Pipeline

ETL stands for Extract, Transform, Load - the fundamental pattern of data processing. You extract data from sources (JSON APIs, Excel files), transform it (clean, calculate, reshape), and load it to destinations (reports, databases). Let's build a pipeline that combines JSON, Excel, and NumPy to process student performance data. This real-world example shows how different formats work together.

In [ ]:
# Step 1: Extract - Load JSON configuration
analysis_config = {
    "analysis_name": "Student Performance Q1 2025",
    "thresholds": {
        "passing": 60,
        "excellence": 90,
        "warning": 70
    },
    "weights": {
        "exams": 0.6,
        "assignments": 0.4
    }
}

# Save configuration
with open('analysis_config.json', 'w') as f:
    json.dump(analysis_config, f, indent=2)

print("Configuration created")

In [ ]:
# Step 2: Transform - Process student data with NumPy
# Create sample exam and assignment scores
np.random.seed(42)
exam_scores = np.random.normal(75, 12, size=(10, 3))  # 10 students, 3 exams
assignment_scores = np.random.normal(82, 8, size=(10, 4))  # 10 students, 4 assignments

# Clip to valid range (0-100)
exam_scores = np.clip(exam_scores, 0, 100)
assignment_scores = np.clip(assignment_scores, 0, 100)

# Calculate averages using NumPy
exam_avg = exam_scores.mean(axis=1)
assignment_avg = assignment_scores.mean(axis=1)

print("Calculated averages for 10 students")

In [ ]:
# Step 3: Load - Create comprehensive Excel report
# Prepare data for Excel
students = [f"Student_{i+1}" for i in range(10)]
report_data = pd.DataFrame({
    'Student': students,
    'Exam_Average': exam_avg.round(1),
    'Assignment_Average': assignment_avg.round(1),
    'Final_Grade': (
        exam_avg * analysis_config['weights']['exams'] + 
        assignment_avg * analysis_config['weights']['assignments']
    ).round(1)
})

# Add status based on thresholds
report_data['Status'] = report_data['Final_Grade'].apply(
    lambda x: 'Excellence' if x >= 90 else 
             'Passing' if x >= 60 else 'Failing'
)

print(report_data.head())

In [ ]:
# Create final Excel report with multiple sheets
with pd.ExcelWriter('performance_report.xlsx', engine='openpyxl') as writer:
    # Main report
    report_data.to_excel(writer, sheet_name='Final Grades', index=False)
    
    # Detailed exam scores
    exam_df = pd.DataFrame(exam_scores, columns=['Exam 1', 'Exam 2', 'Exam 3'])
    exam_df.insert(0, 'Student', students)
    exam_df.to_excel(writer, sheet_name='Exam Details', index=False)
    
    # Summary statistics
    summary = report_data['Status'].value_counts().to_frame()
    summary.to_excel(writer, sheet_name='Summary')

print("\nCreated comprehensive performance report!")

### Format Conversion Functions

In real-world data processing, you often need to convert between formats. A web API might send JSON that needs to become an Excel report, or you might need to load Excel data for NumPy analysis. Here are reusable functions for common conversions. These utility functions form the backbone of many data processing pipelines.

In [ ]:
def json_to_excel(json_file, excel_file):
    """Convert JSON file to Excel format."""
    # Load JSON
    with open(json_file, 'r') as f:
        data = json.load(f)
    
    # Convert to DataFrame and save
    if isinstance(data, list):
        df = pd.DataFrame(data)
        df.to_excel(excel_file, index=False)
        return True
    return False

# Test the conversion
test_data = [
    {"name": "Alice", "score": 92},
    {"name": "Bob", "score": 88}
]
with open('test.json', 'w') as f:
    json.dump(test_data, f)

json_to_excel('test.json', 'test_converted.xlsx')
print("Converted JSON to Excel successfully!")

### Exercise 4: Complete Data Pipeline

Create a pipeline that:
1. Loads product data from JSON
2. Uses NumPy to calculate statistics
3. Exports results to Excel with proper formatting

In [ ]:
# Product data in JSON format
products_json = [
    {"name": "Laptop", "sales": [45, 52, 48, 61, 55]},
    {"name": "Tablet", "sales": [30, 28, 35, 40, 38]},
    {"name": "Phone", "sales": [120, 115, 125, 130, 128]}
]

# TODO: Save as JSON, calculate statistics with NumPy,
# create Excel report with average and total sales
# Your code here:

In [ ]:
# Solution 4
# Save product data as JSON
with open('products.json', 'w') as f:
    json.dump(products_json, f)

# Load and process with NumPy
with open('products.json', 'r') as f:
    products = json.load(f)

# Calculate statistics
report_data = []
for product in products:
    sales_array = np.array(product['sales'])
    report_data.append({
        'Product': product['name'],
        'Average Sales': sales_array.mean(),
        'Total Sales': sales_array.sum(),
        'Best Month': sales_array.max()
    })

# Create Excel report
report_df = pd.DataFrame(report_data)
report_df.to_excel('product_analysis.xlsx', index=False)
print("Pipeline complete! Check product_analysis.xlsx")

## Part 5: Practical Application - Student Analytics System

### Building a Complete System

Let's combine everything we've learned into a professional student analytics system. This system uses JSON for configuration, Excel for data input/output, and NumPy for high-performance calculations. This is exactly how real data applications are built - combining the strengths of each tool for a complete solution.

In [ ]:
class StudentAnalytics:
    """Complete analytics system using JSON, Excel, and NumPy."""
    
    def __init__(self, config_file):
        # Load configuration from JSON
        with open(config_file, 'r') as f:
            self.config = json.load(f)
        print(f"Loaded config: {self.config['analysis_name']}")
        
    def generate_sample_data(self, n_students=15):
        """Generate sample student data for testing."""
        np.random.seed(42)
        
        # Create student info
        students = []
        for i in range(n_students):
            students.append({
                'StudentID': f'S{i+1:03d}',
                'Name': f'Student_{i+1}',
                'Year': np.random.choice([1, 2, 3, 4])
            })
        
        # Create grades using NumPy
        grades = np.random.normal(78, 15, size=(n_students, 5))
        grades = np.clip(grades, 0, 100)
        
        return pd.DataFrame(students), grades

In [ ]:
# Create config and initialize system
config = {
    "analysis_name": "Fall 2024 Final Analysis",
    "thresholds": {"passing": 60, "warning": 70, "excellence": 90},
    "grade_weights": [0.15, 0.15, 0.20, 0.20, 0.30]  # 5 assignments
}

with open('analytics_config.json', 'w') as f:
    json.dump(config, f, indent=2)

# Initialize analytics system
analytics = StudentAnalytics('analytics_config.json')

In [ ]:
# Generate and process data
students_df, grades_array = analytics.generate_sample_data()

# Use NumPy for weighted grade calculation
weights = np.array(config['grade_weights'])
weighted_grades = grades_array @ weights  # Matrix multiplication

# Add final grades to student data
students_df['Final_Grade'] = weighted_grades.round(1)
students_df['Status'] = students_df['Final_Grade'].apply(
    lambda x: 'Excellence' if x >= 90 else
             'Passing' if x >= 60 else 'Failing'
)

print("Processed grades for all students")
print(students_df.head())

In [ ]:
# Create comprehensive Excel report
with pd.ExcelWriter('final_analytics_report.xlsx', engine='openpyxl') as writer:
    # Student summary
    students_df.to_excel(writer, sheet_name='Student Summary', index=False)
    
    # Detailed grades
    detailed_grades = pd.DataFrame(
        grades_array, 
        columns=['Quiz1', 'Quiz2', 'Midterm', 'Project', 'Final']
    )
    detailed_grades.insert(0, 'StudentID', students_df['StudentID'])
    detailed_grades.to_excel(writer, sheet_name='Detailed Grades', index=False)
    
    # Statistics
    stats = {
        'Metric': ['Class Average', 'Highest Grade', 'Lowest Grade', 
                   'Pass Rate (%)', 'Excellence Rate (%)'],
        'Value': [
            weighted_grades.mean().round(1),
            weighted_grades.max().round(1),
            weighted_grades.min().round(1),
            (weighted_grades >= 60).mean() * 100,
            (weighted_grades >= 90).mean() * 100
        ]
    }
    stats_df = pd.DataFrame(stats)
    stats_df.to_excel(writer, sheet_name='Class Statistics', index=False)

print("\nCreated final analytics report with 3 sheets!")

## Summary and Key Takeaways

Congratulations! You've mastered three essential tools for modern data processing:

1. **JSON**: Perfect for APIs, configuration files, and structured data exchange
   - Handle nested structures with safe navigation
   - Always validate and handle errors when loading external JSON
   - Use pretty printing for debugging complex structures

2. **Excel**: The business world's data format
   - Create multi-sheet workbooks with pandas ExcelWriter
   - Read specific sheets or entire workbooks
   - Add formatting and summaries for professional reports

3. **NumPy**: Foundation for numerical computing
   - Arrays are 50-100x faster than lists for math operations
   - Vectorized operations eliminate the need for loops
   - Boolean indexing provides powerful data filtering

4. **Integration**: Combine formats for complete solutions
   - JSON for configuration and APIs
   - Excel for business users and reports
   - NumPy for fast calculations and analysis

Remember: Choose the right tool for each job. JSON for flexibility, Excel for business compatibility, and NumPy for performance. Most real applications use all three!

## Clean Up

Let's remove the temporary files we created during this lesson to keep your workspace clean.

In [ ]:
# List of files to clean up
files_to_remove = [
    'app_config.json', 'student_records.xlsx', 'student_report.xlsx',
    'sales_report.xlsx', 'analysis_config.json', 'test.json',
    'test_converted.xlsx', 'products.json', 'product_analysis.xlsx',
    'analytics_config.json', 'performance_report.xlsx',
    'final_analytics_report.xlsx'
]

# Remove files
for filename in files_to_remove:
    if os.path.exists(filename):
        os.remove(filename)
        print(f"Removed: {filename}")

print("\nCleanup complete! Your workspace is clean.")